[![Open In Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/neuromatch/climate-course-content/blob/main/tutorials/W2D3_FutureClimate-IPCCII&amp;IIISocio-EconomicBasis/W2D3_Tutorial2.ipynb)   <a href="https://kaggle.com/kernels/welcome?src=https://raw.githubusercontent.com/neuromatch/climate-course-content/main/tutorials/W2D3_FutureClimate-IPCCII&amp;IIISocio-EconomicBasis/W2D3_Tutorial2.ipynb" target="_blank"><img alt="Open in Kaggle" src="https://kaggle.com/static/images/open-in-kaggle.svg"/></a>

# Tutorial 2: Fossil Fuel Emissions, Growth, and Damage
**Week 2, Day 3: The Socioeconomics of Climate Change**

**Content creators:**  Paul Heubel, Maximilian Puelma Touzel

**Content reviewers:** Mujeeb Abdulfatai, Nkongho Ayuketang Arreyndip, Jeffrey N. A. Aryee, Jenna Pearson, Abel Shibu, Ohad Zivan

**Content editors:** Paul Heubel, Jenna Pearson, Chi Zhang, Ohad Zivan

**Production editors:** Wesley Banfield, Paul Heubel, Jenna Pearson, Konstantine Tsafatinos, Chi Zhang, Ohad Zivan

**Our 2024 Sponsors:** CMIP, NFDI4Earth

# Tutorial objectives

*Estimated timing of tutorial:* 30 minutes

This tutorial explores the impact of population and economic growth on the global temperature and how a changing climate due to fossil fuel emissions damages our economy. You model these scenarios by 'controlling the knobs' of the Climate Solution Simulator named [En-ROADS](https://www.climateinteractive.org/en-roads/).

After finishing this tutorial you can

* discuss the impact of a growth-based economy on future fossil-fuel emissions along the Kaya identity
* qualitatively describe the impact of population and economic growth on the global temperature within the En-ROADS model environment.
* (explain qualitatively how a different damage function formulation impacts the economic activity)

In [ ]:
# import
import matplotlib.pyplot as plt

##  Figure settings


In [ ]:
# @title Figure settings
import ipywidgets as widgets  # interactive display

%config InlineBackend.figure_format = 'retina'
plt.style.use(
    "https://raw.githubusercontent.com/neuromatch/climate-course-content/main/cma.mplstyle"
)

##  Helper functions


In [ ]:
# @title Helper functions

def pooch_load(filelocation=None, filename=None, processor=None):
    shared_location = "/home/jovyan/shared/Data/tutorials/W2D3_FutureClimate-IPCCII&IIISocio-EconomicBasis"  # this is different for each day
    user_temp_cache = tempfile.gettempdir()

    if os.path.exists(os.path.join(shared_location, filename)):
        file = os.path.join(shared_location, filename)
    else:
        file = pooch.retrieve(
            filelocation,
            known_hash=None,
            fname=os.path.join(user_temp_cache, filename),
            processor=processor,
        )

    return file

##  Video 1: Orienting in a 'Climate Solution' Simulator


In [ ]:
# @title Video 1: Orienting in a 'Climate Solution' Simulator

from ipywidgets import widgets
from IPython.display import YouTubeVideo
from IPython.display import IFrame
from IPython.display import display


class PlayVideo(IFrame):
  def __init__(self, id, source, page=1, width=400, height=300, **kwargs):
    self.id = id
    if source == 'Bilibili':
      src = f'https://player.bilibili.com/player.html?bvid={id}&page={page}'
    elif source == 'Osf':
      src = f'https://mfr.ca-1.osf.io/render?url=https://osf.io/download/{id}/?direct%26mode=render'
    super(PlayVideo, self).__init__(src, width, height, **kwargs)


def display_videos(video_ids, W=400, H=300, fs=1):
  tab_contents = []
  for i, video_id in enumerate(video_ids):
    out = widgets.Output()
    with out:
      if video_ids[i][0] == 'Youtube':
        video = YouTubeVideo(id=video_ids[i][1], width=W,
                             height=H, fs=fs, rel=0)
        print(f'Video available at https://youtube.com/watch?v={video.id}')
      else:
        video = PlayVideo(id=video_ids[i][1], source=video_ids[i][0], width=W,
                          height=H, fs=fs, autoplay=False)
        if video_ids[i][0] == 'Bilibili':
          print(f'Video available at https://www.bilibili.com/video/{video.id}')
        elif video_ids[i][0] == 'Osf':
          print(f'Video available at https://osf.io/{video.id}')
      display(video)
    tab_contents.append(out)
  return tab_contents


video_ids = [('Youtube', 'g5VRHCcIyxk'),
             #('Bilibili', 'BV1nN411U75L')
            ]
tab_contents = display_videos(video_ids, W=730, H=410)
tabs = widgets.Tab()
tabs.children = tab_contents
for i in range(len(tab_contents)):
  tabs.set_title(i, video_ids[i][0])
display(tabs)

In [ ]:
# @markdown
from ipywidgets import widgets
from IPython.display import IFrame

link_id = "mtyrb"

download_link = f"https://osf.io/download/{link_id}/"
render_link = f"https://mfr.ca-1.osf.io/render?url=https://osf.io/{link_id}/?direct%26mode=render%26action=download%26mode=render"
# @markdown
out = widgets.Output()
with out:
    print(f"If you want to download the slides: {download_link}")
    display(IFrame(src=f"{render_link}", width=730, height=410))
display(out)

# Section 1: Quantification of Fossil Fuel Emissions and Its Dependency on Growth

We discussed in the slides how economics represents the human population as a source of labor needed to produce goods and services. A by-product of this production are fossil fuel emissions, which increase atmospheric greenhouse gas (GHG) concentrations, significantly changing the earth's climate. Let us take a look at the relationship between people, production, and emissions in more detail using the En-ROADS simulator.

You might already have clicked through the toggles at the top of the control panel of En-ROADS and tried the different *Views* (Main graphs, Kaya graphs, Miniature graphs). Select now the **Kaya graphs** view and reset the simulator (click on the anti-clockwise circular arrow to 'Reset all policies & assumptions' or just reload the page/model [here](https://en-roads.climateinteractive.org/)).

The Kaya graphs depict four drivers of growth in carbon dioxide emissions from energy use, which reflects about two-thirds of all greenhouse gas emissions (the remaining third of emissions are from land use changes and other gases, such as methane (CH4) and nitrous oxide (N2O), which are not considered here). The corresponding equation, the so-called [***Kaya identity***](https://en.wikipedia.org/wiki/Kaya_identity) below was developed by Yoichi Kaya:

***CO$_2$ Emissions from Energy = Global Population × GDP per Capita × Energy Intensity of GDP × Carbon Intensity of Energy***

Where [gross domestic product](https://en.wikipedia.org/wiki/Gross_domestic_product) (GDP) is a measure of economic activity or health.  

In a more mathematical form, this equation is

$$
F = P \times \left[\frac{G}{P}\right] \times \left[\frac{E}{G}\right] \times \left[\frac{F}{E}\right]
$$
 - $F$ (CO$_2$ emissions from energy), 
 - $P$ (global population), 
 - $G$ (world GDP), and 
 - $E$ (global energy consumption).

Decomposing emissions in this way helps to see key contributions and, if we assume that the factors are independent of each other (which is not fully true), distinct ways that we can lower emissions. Each factor in this model is important and extreme reductions in one can offset increases in the others. In our case, our emissions $F$ are increasing over time because the Energy Intensity of GDP $\left[\frac{E}{G}\right] $ and the Carbon Intensity of Energy do not together offset enough of our growing GDP ($G$), which is by definition necessary for a growth-based economy.

The first four graphs in the Kaya view display these four variables $\left(P, \frac{G}{P}, \frac{E}{G}, \frac{F}{E}\right)$, with the fifth plot showing Emissions, $F$. This allows us to compare the importance of, say, economic and population growth on the CO$_2$ emissions and subsequent temperature rise by 2100.

## Exercise 1: Population vs. Economic Growth
*Estimated timing:* 10 minutes

1. **Open En-ROADS** [here](https://en-roads.climateinteractive.org/). *(Note the control panel is available in various languages - check the left of the panel of the simulator that should by default show "English".)*

2. **Develop a scenario**: Turn two *growth* 'control knobs' of En-ROADS, which are the sliders *Economical growth* and *Population growth*.  Use the following [cheatsheet](https://img.climateinteractive.org/2019/09/EnROADS-one-page-guide-to-control-panel-v11-dec-2021.pdf) if needed. 

3. **Answer the following questions**:

*   What can you observe within the *Kaya graph* view? Describe the graphs and interpret them.

Read the following dropdown accessible box if you need more information to interpret the Kaya graphs. 

*Be warned that a reset of all your previous changes might be necessary before. If you would like to save your previous scenario, export it via a click on the* ***Share your scenario*** *button in the top right of the Panel, and select 'Copy Scenario Link'*.

*Note that your changes are reflected in the light blue graph, while the baseline scenario remains a black line.*

<details>
<summary> <font color='darkblue'>Click here for a description of the Kaya identity and the corresponding plots </font></summary>

Here is one way to understand the shown trends over time:

The Global Population ($P$) of 8 billion people is growing and growth is anticipated to be 11 billion by the end of the century, according to UN projections. The rate of growth is slowing over time as people have smaller families.

GDP ($G$) per Capita ($P$) is growing steadily per year, and the model assumes this will continue, mostly as people in rapidly developing countries such as China, India, South Africa, Mexico, Brazil, and Indonesia attain higher standards of living.

Energy Intensity ($E$) of GDP is decreasing over time, due to the world economy becoming more efficient, or using less energy per unit of economic output. Technologies are improving - for example, more efficient cars, buildings, and machines—and economies are shifting from manufacturing to services. The product of global population, GDP per capita, and the energy intensity of GDP is the total amount of energy used by the global economy.

Carbon Intensity of Final Energy, the amount of carbon dioxide emitted by energy use, is expected to slightly decline over time. Overall, this downward trend in carbon intensity is attributed to the gradual shifting away from fossil fuels and towards low-carbon energy sources.

Carbon Dioxide Emissions from Energy are the result of all four factors multiplied together, and you can see that in the Baseline Scenario emissions are growing. As the level of carbon dioxide in the atmosphere correlates with temperature, an increased concentration of carbon dioxide in the atmosphere leads to an increase in global temperatures.

These factors explain, in simple terms, why emissions are increasing in the Baseline Scenario. Improvements in efficiency and decarbonization are not yet keeping up with the strong growth in population and consumption
 
*** 
 
</details>

## Questions 1:
*Estimated timing:* 10 minutes

Before using the sliders and answering the following questions, build a brief working hypothesis. Which one of the two 'growth knobs' do you expect will be more influential on the global mean temperature and also how much more? 

1. What do you observe, when you only change the population growth slider? And vice versa changing only the economic growth slider? 
2. Combine the effect of both sliders in the common and opposite direction, respectively. Are you surprised about the output?

[*Click for solution*](https://github.com/neuromatch/climate-course-content/tree/main/tutorials/W2D3_FutureClimate-IPCCII&IIISocio-EconomicBasis/solutions/W2D3_Tutorial2_Solution_c67833bd.py)



<details>
<summary> <font color='darkblue'>Click here for a bonus digression on the Limits To Growth </font></summary>
    
### Bonus: A note on exponential growth in a bounded system 
Consider a bounded system undergoing only positive feedback leading to exponential growth. The characteristic duration of growth until the system state reaches the system boundary is only weakly sensitive to the size of the boundary. For example, in the context of exponential resource-driven economic growth on Earth, reaching the boundary means exhausting its accessible physical resources. Ten times more or less of the starting amount of accessible resources only changes the time at which those resources are exhausted by a factor of 2 up or down, respectively. 

Physics demands that behind the exponential extraction of resources is an exponential use of an energy resource. In recent times on Earth, this has been fossil fuels, which are non-renewable. Legitimate concerns of peak oil in the late 1990s were quelled by the Shale revolution in the United States and other technological advances in oil and gas exploration and exploitation. These have increased (by a factor between 2 and 4) the total amount of known reserves that can be profitably exploited. While this increase is significant on an linear scale, it is negligible on an exponential scale. Looking forward, the largest estimates for how much larger accessible oil and gas reserves will be are within an order of magnitude of current reserves. Presuming resource-driven growth economics continues, whatever accessible oil and gass is left will then be exhausted within a short period of time (e.g. within a century). 

Exponential growth in a bounded system will often slow as it reaches the boundary because of boundary-sized feedback effects. In our case, demand growth for fossil fuels is starting to slow with the development of renewable energy sources. There still substantial uncertainty about how these feedbacks will play out. Some questions to consider: 
- whether the transition to renewable energy sources can happen before we exhaust the associated non-renewable resources. 
- Once transitioned, whether the non-renewable resource use (e.g. of rare-earth metals) needed to sustain the renewable energy sector is sustainable in a growth-based economics
- Once transitioned, whether this renewable energy resource might not slow, but instead accelerate the extraction of all non-renewable resources (see [Jevon's paradox](https://en.wikipedia.org/wiki/Jevons_paradox)). 

*** 
 
</details>

# Bonus Section 2: The Economic Impact of Climate Change

In the previous day's tutorials, you learned how increases in atmospheric greenhouse gas (GHG) concentrations significantly alter Earth's climate and examined the impacts of these emissions on variables such as sea-surface temperature and oxygen. These changes in climate variables can, in turn, impact the economy. For example, increased temperatures may reduce crop yields or soften road surfaces requiring more frequent or intense repairs.

## Bonus Question 2:

1. Take a minute to think of some other possible ways in which climate change can affect the economy. Then discuss with your pod.

[*Click for solution*](https://github.com/neuromatch/climate-course-content/tree/main/tutorials/W2D3_FutureClimate-IPCCII&IIISocio-EconomicBasis/solutions/W2D3_Tutorial2_Solution_efff427c.py)



These economic impacts on climate change are considered *economic damage* as they typically result in less or slower economic growth. Economists incorporate the impacts of climate change on the economy into models through a **damage function**, which usually represents climate change by an increase in global temperature, and the impact on the economy as a reduction in [gross domestic product](https://en.wikipedia.org/wiki/Gross_domestic_product) (GDP).

You can dive deeper into the control knob functionalities of En-ROADS by changing the quantification of how climate change damages the economy via a reduction in GDP. To have a closer look at the assumptions that go into the model, we click on the 'Simulation' toggle and select 'Assumptions', in the bottom a box of toggles appears. Here we choose the 'Economy' section and click on 'Economic impact of climate change'.

### Bonus Exercise 2: Choose a Damage function
*Estimated timing:* 10 minutes

In this section, 3 dropdowns correspond to 3 assumptions: (1) whether or not climate change slows economic growth, (2) if yes, how strongly as a function of temperature (what is the damage function), and (3) by how much do we discount far future welfare relative to current welfare. 

1. Hypothesize which parameter needs to be changed to have a less severe damage function.

2. Decide which 'related graph' shall be shown on the top left and explain your hypothesis and final choice of the parameter along it.


[*Click for solution*](https://github.com/neuromatch/climate-course-content/tree/main/tutorials/W2D3_FutureClimate-IPCCII&IIISocio-EconomicBasis/solutions/W2D3_Tutorial2_Solution_1425c24a.py)



With this, we already discussed a few damage functions in En-Roads.  Although they are central to the climate-economy connection of the models, their formulation is relatively ad hoc, which leads to validity issues that are often criticized. 

There are at least two fundamental problems with damage functions (for more see [*The appallingly bad neoclassical economics of climate change* by S. Keen in *Globalizations* (2020)](https://www.tandfonline.com/doi/full/10.1080/14747731.2020.1807856)):
1. As mathematical model objects, they are likely too simple to be useful predictors in characterizing climate damages in sufficient complexity. 
2. They arise from a poorly validated model-fitting procedure. In particular, it relies on ad hoc functional forms and the relevance of historical and geographical variability to future variability.

Despite these problems, damage functions allow economists within the neoclassical paradigm to start seriously considering the damaging effects of climate change.

# Summary

In this tutorial, we discussed the impact of growth on fossil fuel emissions, in particular population growth vs. economic growth, and its treatment by the world model En-ROADS. Last but not least we introduced the important concept of the damage function to connect climate and economy within a model.

# Resources

This tutorial is inspired by teaching material from [Climate Interactive](https://climateinteractive.org/) and other documents. 
A few important resources are linked below:

- [En-ROADS documentation](https://docs.climateinteractive.org/projects/en-roads/en/latest/index.html)
- [En-ROADS User Guide PDF](https://docs.climateinteractive.org/projects/en-roads/en/latest/en-roads-user-guide.pdf)
- [Guided Assignment - Simulating Climate Futures in En-ROADS: Short Version](https://www.climateinteractive.org/guided-assignment/)